In [1]:
import pandas as pd
import json

In [2]:
data = pd.read_json('SIR_train_set.json')

In [3]:
columns_1 = ['exploitabilityScore', 'baseScore', 'impactScore', 'severity']
train_data = data[columns_1]
train_data

exploitabilityScore  baseScore  impactScore  severity
0                     3.9        7.5          3.6      HIGH
1                     3.9        9.8          5.9  CRITICAL
2                     3.9        7.5          3.6      HIGH
3                     2.2        8.1          5.9      HIGH
4                     2.8        8.8          5.9      HIGH
...                   ...        ...          ...       ...
5619                  3.9        7.5          3.6      HIGH
5620                  2.8        6.1          2.7    MEDIUM
5621                  2.8        6.5          3.6    MEDIUM
5622                  2.8        6.5          3.6    MEDIUM
5623                  2.3        5.4          2.7    MEDIUM

[5624 rows x 4 columns]

In [4]:
vectorString = data['vectorString']
vectorString

0       CVSS:3.1/AV:N/AC:L/PR:N/UI:N/S:U/C:H/I:N/A:N
1       CVSS:3.1/AV:N/AC:L/PR:N/UI:N/S:U/C:H/I:H/A:H
2       CVSS:3.1/AV:N/AC:L/PR:N/UI:N/S:U/C:H/I:N/A:N
3       CVSS:3.0/AV:N/AC:H/PR:N/UI:N/S:U/C:H/I:H/A:H
4       CVSS:3.1/AV:N/AC:L/PR:N/UI:R/S:U/C:H/I:H/A:H
                            ...                     
5619    CVSS:3.1/AV:N/AC:L/PR:N/UI:N/S:U/C:N/I:N/A:H
5620    CVSS:3.1/AV:N/AC:L/PR:N/UI:R/S:C/C:L/I:L/A:N
5621    CVSS:3.1/AV:N/AC:L/PR:N/UI:R/S:U/C:N/I:H/A:N
5622    CVSS:3.1/AV:N/AC:L/PR:N/UI:R/S:U/C:N/I:H/A:N
5623    CVSS:3.1/AV:N/AC:L/PR:L/UI:R/S:C/C:L/I:L/A:N
Name: vectorString, Length: 5624, dtype: object

In [5]:
# 打开并读取JSON文件
with open('label_word_ids_CVSS2.json', 'r') as file:
    # 解析JSON文件
    cvss2 = json.load(file)
cvss2

{'AV': {'network': 2897, 'adjacent': 5516, 'local': 2334},
 'AC': {'low': 2659, 'medium': 5396, 'high': 2152},
 'Au': {'none': 3904, 'single': 2309, 'multiple': 3674},
 'C': {'none': 3904, 'partial': 7704, 'complete': 3143},
 'I': {'none': 3904, 'partial': 7704, 'complete': 3143},
 'A': {'none': 3904, 'partial': 7704, 'complete': 3143},
 'severity': {'low': 2659, 'medium': 5396, 'high': 2152}}

In [6]:
# 打开并读取JSON文件
with open('label_word_ids.json', 'r') as file:
    # 解析JSON文件
    cvss = json.load(file)
cvss['AV']
len(cvss)

9

In [22]:
columns_2 = ['AV', 'AC', 'PR', 'UI', 'S', 'C', 'I', 'A']
for column in columns_2:
    cvss[column] = {k[0].upper(): v for k, v in cvss[column].items()}
# 计算每一行的总值
summ = {key: sum(values.values()) for key, values in cvss.items()}

# 计算每个值除以总值
cvss = {
    key: {subkey: value / summ[key] for subkey, value in values.items()}
    for key, values in cvss.items()
}
cvss

{'AV': {'N': 0.20251660258650825,
  'A': 0.3855994407549808,
  'L': 0.1631597343586159,
  'P': 0.24872422229989516},
 'AC': {'L': 0.5526917480773228, 'H': 0.4473082519226772},
 'PR': {'N': 0.44796328169822147,
  'L': 0.3051061388410786,
  'H': 0.24693057946069993},
 'UI': {'N': 0.5477760628595482, 'R': 0.4522239371404518},
 'S': {'U': 0.8439380911435942, 'C': 0.15606190885640583},
 'C': {'N': 0.44796328169822147,
  'L': 0.3051061388410786,
  'H': 0.24693057946069993},
 'I': {'N': 0.44796328169822147,
  'L': 0.3051061388410786,
  'H': 0.24693057946069993},
 'A': {'N': 0.44796328169822147,
  'L': 0.3051061388410786,
  'H': 0.24693057946069993},
 'severity': {'low': 0.18472974850632207,
  'medium': 0.37487842156454076,
  'high': 0.14950673891899402,
  'critical': 0.2908850910101431}}

In [23]:
#转换数据
def transform_value(val):
    return val.split(':')[1]
temp = []
for i in range(vectorString.size):
    part =  vectorString[i].split('/')
    list_items = part[1::]
    temp.append(list_items)
train_data_temp = pd.DataFrame(temp, columns=columns_2)
train_data_temp = train_data_temp.applymap(transform_value)
train_data_temp

AV AC PR UI  S  C  I  A
0     N  L  N  N  U  H  N  N
1     N  L  N  N  U  H  H  H
2     N  L  N  N  U  H  N  N
3     N  H  N  N  U  H  H  H
4     N  L  N  R  U  H  H  H
...  .. .. .. .. .. .. .. ..
5619  N  L  N  N  U  N  N  H
5620  N  L  N  R  C  L  L  N
5621  N  L  N  R  U  N  H  N
5622  N  L  N  R  U  N  H  N
5623  N  L  L  R  C  L  L  N

[5624 rows x 8 columns]

In [24]:
# 替换 DataFrame 中的值
train_data_temp.replace(cvss, inplace=True)
train_data_temp

AV        AC        PR        UI         S         C         I  \
0     0.202517  0.552692  0.447963  0.547776  0.843938  0.246931  0.447963   
1     0.202517  0.552692  0.447963  0.547776  0.843938  0.246931  0.246931   
2     0.202517  0.552692  0.447963  0.547776  0.843938  0.246931  0.447963   
3     0.202517  0.447308  0.447963  0.547776  0.843938  0.246931  0.246931   
4     0.202517  0.552692  0.447963  0.452224  0.843938  0.246931  0.246931   
...        ...       ...       ...       ...       ...       ...       ...   
5619  0.202517  0.552692  0.447963  0.547776  0.843938  0.447963  0.447963   
5620  0.202517  0.552692  0.447963  0.452224  0.156062  0.305106  0.305106   
5621  0.202517  0.552692  0.447963  0.452224  0.843938  0.447963  0.246931   
5622  0.202517  0.552692  0.447963  0.452224  0.843938  0.447963  0.246931   
5623  0.202517  0.552692  0.305106  0.452224  0.156062  0.305106  0.305106   

             A  
0     0.447963  
1     0.246931  
2     0.447963  
3     0.246931  
4     0.246931  
...        ...  
5619  0.246931  
5620  0.447963  
5621  0.447963  
5622  0.447963  
5623  0.447963  

[5624 rows x 8 columns]

In [28]:
train_data = pd.concat([train_data_temp, train_data], axis=1)
train_data

AV        AC        PR        UI         S         C         I  \
0     0.202517  0.552692  0.447963  0.547776  0.843938  0.246931  0.447963   
1     0.202517  0.552692  0.447963  0.547776  0.843938  0.246931  0.246931   
2     0.202517  0.552692  0.447963  0.547776  0.843938  0.246931  0.447963   
3     0.202517  0.447308  0.447963  0.547776  0.843938  0.246931  0.246931   
4     0.202517  0.552692  0.447963  0.452224  0.843938  0.246931  0.246931   
...        ...       ...       ...       ...       ...       ...       ...   
5619  0.202517  0.552692  0.447963  0.547776  0.843938  0.447963  0.447963   
5620  0.202517  0.552692  0.447963  0.452224  0.156062  0.305106  0.305106   
5621  0.202517  0.552692  0.447963  0.452224  0.843938  0.447963  0.246931   
5622  0.202517  0.552692  0.447963  0.452224  0.843938  0.447963  0.246931   
5623  0.202517  0.552692  0.305106  0.452224  0.156062  0.305106  0.305106   

             A  exploitabilityScore  baseScore  impactScore  severity  
0     0.447963                  3.9        7.5          3.6      HIGH  
1     0.246931                  3.9        9.8          5.9  CRITICAL  
2     0.447963                  3.9        7.5          3.6      HIGH  
3     0.246931                  2.2        8.1          5.9      HIGH  
4     0.246931                  2.8        8.8          5.9      HIGH  
...        ...                  ...        ...          ...       ...  
5619  0.246931                  3.9        7.5          3.6      HIGH  
5620  0.447963                  2.8        6.1          2.7    MEDIUM  
5621  0.447963                  2.8        6.5          3.6    MEDIUM  
5622  0.447963                  2.8        6.5          3.6    MEDIUM  
5623  0.447963                  2.3        5.4          2.7    MEDIUM  

[5624 rows x 12 columns]